In [1]:
import numpy as np
import trimesh
import gltfshapes.cube_evenly_sampled
import gltfshapes.linear_samples
import gltfshapes.surface

# Evenly sampled cube of data

Generate some sample data: A 50x50x50 cube of values
We delete all the non-surface data of the cube (set them to NaN) to speed up rendering. In real cases, you might want to keep all voxels, including internal ones depending on how you plan on visualizing and filtering the output.

In [2]:
N = 50

xi, yi, zi = np.meshgrid(*[np.arange(N)] * 3, indexing="ij")
v = np.sin(np.pi * xi * 20 / N) + np.sin(np.pi * yi * 10 / N) + np.sin(np.pi * zi / N)

v[1:-1,1:-1,1:-1] = np.nan

In [3]:
mesh = gltfshapes.cube_evenly_sampled.to_mesh(v)

scene = trimesh.scene.Scene()
scene.add_geometry(mesh, node_name="Simulated values")
scene.show()

# Linear segments of samples

Generate some sample data - two bars unevenly sized segments, each with a value:

In [5]:
def make_bar(fn):
    z = np.linspace(0, 1, 20)
    v = fn(z)
    z = np.e**(2 * z)
    z1 = z[:-1]
    z2 = z[1:]
    v = v[1:]
    x = np.full(len(v), 0)
    y = np.full(len(v), 0)
    return x, y, z1, z2, v

x1, y1, z11, z12, v1 = make_bar(lambda z: np.sin(4 * np.pi * z))
x2, y2, z21, z22, v2 = make_bar(lambda z: np.sin(2*np.pi * z))

x2 += 3
x = np.concatenate((x1, x2))
y = np.concatenate((y1, y2))
z1 = np.concatenate((z11, z21))
z2 = np.concatenate((z12, z22))
v = np.concatenate((v1, v2))


In [6]:
mesh = gltfshapes.linear_samples.to_mesh(x, y, z1, z2, v)

scene = trimesh.scene.Scene()
scene.add_geometry(mesh, node_name="Simulated values")
scene.show()

In [68]:
# Make an undulating surface
a, b = np.meshgrid(np.sin(np.linspace(0, 4*np.pi, 100)), np.sin(np.linspace(0, 16*np.pi, 100)))
surface = a + b

In [71]:
# Make some cutouts at the edges of the surface
xs, ys = np.meshgrid(np.arange(surface.shape[0]), np.arange(surface.shape[1]))

surface[xs < (np.sin(np.linspace(0, 4*np.pi, 100).reshape((100,1))) * 5 + 5)] = np.nan
surface[xs > 100 - (np.sin(np.pi/2 + np.linspace(0, 4*np.pi, 100).reshape((100,1))) * 5 + 5)] = np.nan

In [72]:
scene = trimesh.scene.Scene()
scene.add_geometry(
    gltfshapes.surface.to_mesh(surface),
    node_name="Simulated values")
scene.show()